In [118]:
import pandas as pd
from itertools import takewhile
import xml.etree.ElementTree as ET
import pymongo
import os

VINA_RESULT_FILENAME="docking_logs.txt"
LIGAND_DIR_LIST_FILENAME = 'list_ligand_dirs.txt'
XML_REPORT_LIST_FILENAME = 'list_xml_reports.txt'

In [26]:
def covert_table_to_dict(table):
    """
    Convert markdown table to Dictionary
    """
    table_splitted = table.split('\n', 1)
    
    if len(table_splitted) != 2:
        print("Invalid table format detected.")
        return None
    
    data = []
    # Get First Header Line
    columns = table_splitted[0].split('|')
    def rename_columns(c):
        c = c.strip().replace('.', "").replace(" ", "_")
        if c.startswith('affinity'):
            c = "affinity"
        return c
    columns = list(map(rename_columns, columns))
    # columns = [c.strip().replace('.', "").replace(" ", "_") for c in columns]
    for line in table_splitted[1].split('\n'):
        row = dict()
        if (not line.startswith('-')):
            cells = line.split('|')
            if(len(cells)) > 1:
                for i, c in enumerate(cells):
                    row[columns[i]] = float(cells[i].strip())
                data.append(row)
    return data
        

In [14]:
def collect_result_from_vina_log(receptordir, ligdir, verbose=False):
    if verbose == True:
        print(f"Processing {receptordir} > {ligdir}")
        
    with open(f"../docking_runs_vina/{receptordir}/{ligdir}/{VINA_RESULT_FILENAME}") as logfile:
        result_table=""
        capture = False
        for line in logfile:
            if line.startswith('[ENDRESULT]'):
                break
            if capture:
                if not line.startswith('[REMARK]'):
                    result_table += line
            if line.startswith('[RESULT]'):
                capture = True
        
        if not result_table:
            print(f"Docking Result Table not found for {receptordir} > {ligdir}")
            return None
        else:
            data = covert_table_to_dict(result_table)
            # Split Ligand ID and Tautomer
            ligname, tautomer = ligdir.split('_')
            # Append ligand to data
            def appender_func(r):
                r['receptor'] = receptordir
                r['ligand'] = ligname
                r['tautomer'] = tautomer
                r['_id'] = str(f"{receptordir}-{ligname}-{tautomer}-m{int(r['mode'])}").lower()
                return r
            data = [appender_func(r) for r in data]
            return data

In [109]:
def xml_to_dict(xmltag):
    if len(xmltag) > 0:
        child_names = [t.tag for t in list(xmltag)]
        data = None
        xml_array_tagnames = [
            'members', 
            'bs_residues', 
            'hydrophobic_interactions', 
            'hydrogen_bonds', 
            'water_bridges',
            'salt_bridges',
            'pi_stacks',
            'pi_cation_interactions',
            'halogen_bonds',
            'metal_complexes',
            'prot_idx_list',
            'lig_idx_list'
        ]
        # If contains duplicates parse as array
        if any(child_names.count(e) > 1 for e in child_names) or (xmltag.tag in xml_array_tagnames):
            data = []
            for child in xmltag:
                #_d = dict()
                #if len(key):
                #    #print(list(key))
                #    _d[key.tag] = list(map(xml_to_dict, list(key)))
                #else:
                #    _d[key.tag] = key.text
                #    _d['attributes'] = key.attrib
                data.append(xml_to_dict(child))
        else:
            data = dict()
            # Else parse as object
            for child in xmltag:
                cdata = xml_to_dict(child)
                data[child.tag] = cdata
            
        return data
    else:
        #data = dict()
        #data[xmltag.tag] = xmltag.text
        if bool(xmltag.attrib) == True:
            return ({
                "value": xmltag.text,
                "attributes": xmltag.attrib
            })
        return xmltag.text.strip().strip("\n") if xmltag.text is not None else None

def parse_xml(xmlfile):
    # create element tree object
    tree = ET.parse(xmlfile)
  
    # get root element
    root = tree.getroot()
    
    bindingsite_data = []
    # iterate news items
    for bindingsite in root.findall('bindingsite'):
        data = xml_to_dict(bindingsite)
        #print(data)
        bindingsite_data.append(data)
        
    return bindingsite_data

#parse_xml(f"../docking_runs_vina/1hny/PE000010_1/reports/complex_pose_2/report.xml")

In [127]:
schema = {
    'identifiers': {
        'longname': str,
        'ligtype': str,
        'hetid': str,
        'chain': str,
        'position': int,
        'composite': bool,
        'members': [
            {'value': str, 'attributes': {'id': int}}
        ],
        'smiles': str,
        'inchikey': str
    },
    'lig_properties': {
        'num_heavy_atoms': int,
        'num_hbd': int,
        'num_unpaired_hbd': int,
        'num_hba': int,
        'num_unpaired_hba': int,
        'num_hal': int,
        'num_unpaired_hal': int,
        'num_aromatic_rings': int,
        'num_rotatable_bonds': int,
        'molweight': float,
        'logp': float
    },
    'interacting_chains': {
        'interacting_chain': {
            'value': str,
            'attributes': {'id': int}
        }
    },
    'bs_residues': [{
        'value': str,
        'attributes': {
            'id': int,
            'contact': bool,
            'min_dist': float,
            'aa': str
        }
    }],
    'interactions': {
        'hydrophobic_interactions': [{
            'resnr': int,
            'restype': str,
            'reschain': str,
            'resnr_lig': int,
            'restype_lig': str,
            'reschain_lig': str,
            'dist': float,
            'ligcarbonidx': int,
            'protcarbonidx': int,
            'ligcoo': {'x': float, 'y': float, 'z': float},
            'protcoo': {'x': float, 'y': float, 'z': float}
        }],
        'hydrogen_bonds': [{
            'resnr': int,
            'restype': str,
            'reschain': str,
            'resnr_lig': int,
            'restype_lig': str,
            'reschain_lig': str,
            'sidechain': bool,
            'dist_h-a': float,
            'dist_d-a': float,
            'don_angle': float,
            'protisdon': bool,
            'donoridx': int,
            'donortype': str,
            'acceptoridx': int,
            'acceptortype': str,
            'ligcoo': {'x': float, 'y': float, 'z': float},
            'protcoo': {'x': float, 'y': float, 'z': float}
        }],
        'salt_bridges': [{
            'resnr': str,
            'restype': str,
            'reschain': str,
            'prot_idx_list': [{'value': int, 'attributes': {'id': int}}],
            'resnr_lig': int,
            'restype_lig': str,
            'reschain_lig': str,
            'dist': float,
            'protispos': bool,
            'lig_group': str,
            'lig_idx_list': [{'value': int, 'attributes': {'id': int}},
            {'value': int, 'attributes': {'id': int}}],
            'ligcoo': {'x': float, 'y': float, 'z': float},
            'protcoo': {'x': float, 'y': float, 'z': float}
        }],
        'pi_stacks': [{
            'resnr': int,
            'restype': str,
            'reschain': str,
            'resnr_lig': int,
            'restype_lig': str,
            'reschain_lig': str,
            'prot_idx_list': [{'value': int, 'attributes': {'id': int}}],
            'centdist': float,
            'angle': float,
            'offset': float,
            'type': str,
            'lig_idx_list': [{'value': int, 'attributes': {'id': int}}],
            'ligcoo': {'x': float, 'y': float, 'z': float},
            'protcoo': {'x': float, 'y': float, 'z': float}
        }],
        'water_bridges': [{
            'resnr': int,
            'restype': str,
            'reschain': str,
            'resnr_lig': int,
            'restype_lig': str,
            'reschain_lig': str,
            'dist_a-w': float, 
            'dist_d-w': float,
            'donor_idx': int,
            'donortype': str,
            'acceptor_idx': int,
            'acceptortype': str,
            'protisdon': bool, 
            'water_idx': int,
            'don_angle': float,
            'water_angle': float,
            'ligcoo': {'x': float, 'y': float, 'z': float},
            'protcoo': {'x': float, 'y': float, 'z': float},
            'watercoo': {'x': float, 'y': float, 'z': float}
        }], 
        'pi_cation_interactions': [{
            'resnr': int,
            'restype': str,
            'reschain': str,
            'resnr_lig': int,
            'restype_lig': str,
            'reschain_lig': str,
            'dist': float,
            'offset': float,
            'protcharged': bool, 
            'prot_idx_list': [{'value': int, 'attributes': {'id': int}}],
            'lig_group': str, 
            'lig_idx_list': [{'value': int, 'attributes': {'id': int}}],
            'ligcoo': {'x': float, 'y': float, 'z': float},
            'protcoo': {'x': float, 'y': float, 'z': float}
        }],
        'halogen_bonds': [{
            'resnr': int,
            'restype': str,
            'reschain': str,
            'resnr_lig': int,
            'restype_lig': str,
            'reschain_lig': str,
            'sidechain': str,
            'dist': float,
            'don_angle': float,
            'acc_angle': float,
            'don_idx': int,
            'donortype': str,
            'acc_idx': int,
            'acceptortype': str,
            'ligcoo': {'x': float, 'y': float, 'z': float},
            'protcoo': {'x': float, 'y': float, 'z': float}
            
        }],
        'metal_complexes': [{
            'resnr': int,
            'restype': str,
            'reschain': str,
            'resnr_lig': int,
            'restype_lig': str,
            'reschain_lig': str,
            'metal_idx': int, 
            'metal_type': str,
            'target_idx': int, 
            'target_type': str,
            'coordination': str, 
            'dist': float, 
            'location': str, 
            'rms': float, 
            'geometry': str, 
            'complexnum': float, 
            'metalcoo': {'x': float, 'y': float, 'z': float},
            'targetcoo': {'x': float, 'y': float, 'z': float}
        }]
    },
    'mappings': {'smiles_to_pdb': str }
}
    

In [126]:
# bs_test = parse_xml(f"../docking_runs_vina/1hny/PE000010_1/reports/complex_pose_2/report.xml")
bs_test = parse_xml("/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000016_1/reports/complex_pose_9/report.xml")
bs_test[0]

{'identifiers': {'longname': 'UNL',
  'ligtype': 'SMALLMOLECULE',
  'hetid': 'UNL',
  'chain': 'd',
  'position': '1',
  'composite': 'False',
  'members': [{'value': 'UNL:d:1', 'attributes': {'id': '1'}}],
  'smiles': '[O]O[C@@H]1C[C@@H]([O])[C@@H]2[C@H](C1)O[C@@H]([C@H](C2)O[C@@H]([C@H]([C@H](C[O])[O])[O])C[C@@]1([O])[C@H](O)O[C@H]([C@H]([C@@H]1[O])[O])C)[C@H]1CC=C([C@@H]2[C@@H]1CO2)[O].C',
  'inchikey': 'HYPACKHHYINBPE-NBSIQOPHSA-N'},
 'lig_properties': {'num_heavy_atoms': '43',
  'num_hbd': '10',
  'num_unpaired_hbd': '8',
  'num_hba': '15',
  'num_unpaired_hba': '11',
  'num_hal': '0',
  'num_unpaired_hal': '0',
  'num_aromatic_rings': '2',
  'num_rotatable_bonds': '9',
  'molweight': '615.6002600000002',
  'logp': '0.7463000000000011'},
 'interacting_chains': {'interacting_chain': {'value': 'A',
   'attributes': {'id': '1'}}},
 'bs_residues': [{'value': '151A',
   'attributes': {'id': '1',
    'contact': 'True',
    'min_dist': '3.6',
    'aa': 'TYR'}},
  {'value': '306A',
   'at

In [128]:
def cast_as_type(datatype, value):
    if value == None:
        return None
    
    if datatype == str:
        return str(value)
    elif datatype == int:
        return int(value)
    elif datatype == float:
        return float(value)
    elif datatype == bool:
        return bool(value)
    else:
        print(f"Unknown data type supplied - {datatype}; setting value to None. This may occur due to schema mismatch or Null value.")
        return None

def typeset_dict(data, type_schema):
    if type(data) == dict:
        typed_data = {}
        for k in data.keys():
            #print(k)
            if k not in type_schema.keys():
                print(f"Key {k} is not defined in schema. Keeping value as is.")
                typed_data[k] = data[k]
            else:
                if type(data[k]) == list:
                    if len(type_schema[k]) > 0:
                        typed_data[k] = typeset_dict(data[k], type_schema[k][0])
                    else:
                        print(f"Schema not defined for list in key {k}. Keeping value as is.")
                        typed_data[k] = data[k]
                else:
                    # TODO: check if type_schema[k] exists
                    typed_data[k] = typeset_dict(data[k], type_schema[k])
        return typed_data
    elif type(data) == list:
        typed_data = []
        for item in data:
            # TODO: check if type_schema[k][0] exists
             typed_data.append(typeset_dict(item, type_schema))
        return typed_data
    else:
        return cast_as_type(type_schema, data) 
            
        
typeset_dict(bs_test[0], schema)

{'identifiers': {'longname': 'UNL',
  'ligtype': 'SMALLMOLECULE',
  'hetid': 'UNL',
  'chain': 'd',
  'position': 1,
  'composite': True,
  'members': [{'value': 'UNL:d:1', 'attributes': {'id': 1}}],
  'smiles': '[O]O[C@@H]1C[C@@H]([O])[C@@H]2[C@H](C1)O[C@@H]([C@H](C2)O[C@@H]([C@H]([C@H](C[O])[O])[O])C[C@@]1([O])[C@H](O)O[C@H]([C@H]([C@@H]1[O])[O])C)[C@H]1CC=C([C@@H]2[C@@H]1CO2)[O].C',
  'inchikey': 'HYPACKHHYINBPE-NBSIQOPHSA-N'},
 'lig_properties': {'num_heavy_atoms': 43,
  'num_hbd': 10,
  'num_unpaired_hbd': 8,
  'num_hba': 15,
  'num_unpaired_hba': 11,
  'num_hal': 0,
  'num_unpaired_hal': 0,
  'num_aromatic_rings': 2,
  'num_rotatable_bonds': 9,
  'molweight': 615.6002600000002,
  'logp': 0.7463000000000011},
 'interacting_chains': {'interacting_chain': {'value': 'A',
   'attributes': {'id': 1}}},
 'bs_residues': [{'value': '151A',
   'attributes': {'id': 1, 'contact': True, 'min_dist': 3.6, 'aa': 'TYR'}},
  {'value': '306A',
   'attributes': {'id': 2, 'contact': True, 'min_dist':

In [5]:
client = pymongo.MongoClient("mongodb://localhost:2717/")
db = client["digestive_enzyme_inhibtors"]

In [6]:
# receptor_dirs = ['1hny', '1lpb', '1ose', '1smd', '3axh']
receptor_dirs = ['1hny', '1lpb', '1ose']

# Insert Scoring Reports

In [138]:
def add_report(path):
    # receptordir
    # line - ligand_tautomer dir
    # report report complex dir
    # get binding site reports as dict
    print(path)
    # path = path.rstrip("\n")
    splitted_path = path.split('/')
    path_list_len = len(splitted_path)
    
    complex_dir = splitted_path[path_list_len - 2]
    lig_tautomer_dir = splitted_path[path_list_len - 4]
    receptor_dir = splitted_path[path_list_len - 5]
    
    #bs = parse_xml(f"../docking_runs_vina/{receptordir}/{line}/reports/{report}/report.xml")
    bs = parse_xml(path)
    if len(bs) > 1:
        print(f"Multiple binding site exists for {receptor_dir} > {lig_tautomer_dir} > {complex_dir}. Only first will be considered.")

    if len(bs) > 0:
        rdata = typeset_dict(bs[0], schema)

        ligname, tautomer = lig_tautomer_dir.split('_')
        # Get the pose id (mode) from the report directory name
        mode_id = complex_dir.split('_')
        mode_id = mode_id[len(mode_id) - 1] # last number from string

        rdata['receptor'] = receptor_dir
        rdata['ligand'] = ligname
        rdata['tautomer'] = tautomer
        rdata['binding_mode'] = int(mode_id)
        rdata['report_ligdir'] = lig_tautomer_dir
        rdata['reportdir'] = complex_dir
        rdata['_id'] = str(f"{receptor_dir}-{ligname}-{tautomer}-m{int(mode_id)}").lower()
        collection.insert_one(rdata)
    else:
        print(f"Report not added for {receptor_dir} > {lig_tautomer_dir} > {complex_dir}")                    

In [139]:
#ts = time()
for receptordir in receptor_dirs:
     with open(f"../docking_runs_vina/{receptordir}/{XML_REPORT_LIST_FILENAME}") as listfile:
        for line in listfile:
            line = line.rstrip("\n")
            if os.path.isfile(line):
                add_report(line)
#print(time() - ts)

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_1/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_2/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_3/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_4/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_5/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_6/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_7/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_8/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_9/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_2/repo

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000011_3/reports/complex_pose_8/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000011_3/reports/complex_pose_9/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000012_1/reports/complex_pose_1/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000012_1/reports/complex_pose_2/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000012_1/reports/complex_pose_3/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000012_1/reports/complex_pose_4/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000012_1/reports/complex_pose_5/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000012_1/reports/complex_pose_6/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000012_1/reports/complex_pose_7/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000012_1/repo

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000016_1/reports/complex_pose_6/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000016_1/reports/complex_pose_7/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000016_1/reports/complex_pose_8/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000016_1/reports/complex_pose_9/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000016_2/reports/complex_pose_1/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000016_2/reports/complex_pose_2/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000016_2/reports/complex_pose_3/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000016_2/reports/complex_pose_4/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000016_2/reports/complex_pose_5/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000016_2/repo

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000022_2/reports/complex_pose_8/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000022_2/reports/complex_pose_9/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000022_3/reports/complex_pose_1/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000022_3/reports/complex_pose_2/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000022_3/reports/complex_pose_3/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000022_3/reports/complex_pose_4/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000022_3/reports/complex_pose_5/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000022_3/reports/complex_pose_6/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000022_3/reports/complex_pose_7/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000022_3/repo

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000027_11/reports/complex_pose_3/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000027_11/reports/complex_pose_4/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000027_11/reports/complex_pose_5/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000027_11/reports/complex_pose_6/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000027_11/reports/complex_pose_7/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000027_11/reports/complex_pose_8/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000027_11/reports/complex_pose_9/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000027_12/reports/complex_pose_1/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000027_12/reports/complex_pose_2/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE0000

...

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001023_2/reports/complex_pose_5/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001023_2/reports/complex_pose_6/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001023_2/reports/complex_pose_7/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001023_2/reports/complex_pose_8/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001023_2/reports/complex_pose_9/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001023_3/reports/complex_pose_1/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001023_3/reports/complex_pose_2/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001023_3/reports/complex_pose_3/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001023_3/reports/complex_pose_4/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001023_3/repo

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001028_1/reports/complex_pose_9/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001029_1/reports/complex_pose_1/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001029_1/reports/complex_pose_2/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001029_1/reports/complex_pose_3/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001029_1/reports/complex_pose_4/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001029_1/reports/complex_pose_5/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001029_1/reports/complex_pose_6/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001029_1/reports/complex_pose_7/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001029_1/reports/complex_pose_8/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001029_1/repo

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001041_1/reports/complex_pose_3/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001041_1/reports/complex_pose_4/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001041_1/reports/complex_pose_5/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001041_1/reports/complex_pose_6/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001041_1/reports/complex_pose_7/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001041_1/reports/complex_pose_8/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001041_1/reports/complex_pose_9/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001043_1/reports/complex_pose_1/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001043_1/reports/complex_pose_2/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001043_1/repo

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001057_1/reports/complex_pose_1/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001057_1/reports/complex_pose_2/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001057_1/reports/complex_pose_3/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001057_1/reports/complex_pose_4/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001057_1/reports/complex_pose_5/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001057_1/reports/complex_pose_6/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001057_1/reports/complex_pose_7/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001057_1/reports/complex_pose_8/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001057_1/reports/complex_pose_9/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001057_2/repo

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001060_4/reports/complex_pose_8/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001060_4/reports/complex_pose_9/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001060_5/reports/complex_pose_1/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001060_5/reports/complex_pose_2/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001060_5/reports/complex_pose_3/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001060_5/reports/complex_pose_4/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001060_5/reports/complex_pose_5/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001060_5/reports/complex_pose_6/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001060_5/reports/complex_pose_7/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001060_5/repo

### Code test using multi threading

In [134]:
from queue import Queue
from threading import Thread
from time import time

In [137]:
class ReportAddWorker(Thread):
    def __init__(self, queue):
        Thread.__init__(self)
        self.queue = queue
    
    def run(self):
        while True:
            path = self.queue.get()
            try:
                print(path)
                #add_report(path)
            finally:
                self.queue.task_done()
ts = time()
queue = Queue()
# create 10 worker
for i in range(50):
    worker = ReportAddWorker(queue)
    worker.daemon = True
    worker.start()

for receptordir in receptor_dirs:
     with open(f"../docking_runs_vina/{receptordir}/{XML_REPORT_LIST_FILENAME}") as listfile:
        for line in listfile:
            line = line.rstrip("\n")
            if os.path.isfile(line):
                queue.put(line)
                #add_report(line)
queue.join()
print(time() - ts)

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_1/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_2/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_3/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_4/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_5/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_6/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_7/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_8/report.xml

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_1/reports/complex_pose_9/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000008_2/repo

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000031_27/reports/complex_pose_3/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000031_27/reports/complex_pose_4/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000031_27/reports/complex_pose_5/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000031_27/reports/complex_pose_6/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000031_27/reports/complex_pose_7/report.xml


/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000031_27/reports/complex_pose_8/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000031_27/reports/complex_pose_9/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000031_28/reports/complex_pose_1/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000031_28/reports/complex_pose_2/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE00003

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000062_51/reports/complex_pose_5/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000062_51/reports/complex_pose_6/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000062_51/reports/complex_pose_7/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000062_51/reports/complex_pose_8/report.xml

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000062_51/reports/complex_pose_9/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000062_52/reports/complex_pose_1/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000062_52/reports/complex_pose_2/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000062_52/reports/complex_pose_3/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000062_52/reports/complex_pose_4/report.xml

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE0000

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000201_1/reports/complex_pose_1/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000201_1/reports/complex_pose_2/report.xml

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000201_1/reports/complex_pose_3/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000201_1/reports/complex_pose_4/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000201_1/reports/complex_pose_5/report.xml

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000201_1/reports/complex_pose_6/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000201_1/reports/complex_pose_7/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000201_1/reports/complex_pose_8/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000201_1/reports/complex_pose_9/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000201_2/repor

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000449_1/reports/complex_pose_3/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000449_1/reports/complex_pose_4/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000449_1/reports/complex_pose_5/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000449_1/reports/complex_pose_6/report.xml


/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000449_1/reports/complex_pose_7/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000449_1/reports/complex_pose_8/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000449_1/reports/complex_pose_9/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000449_10/reports/complex_pose_1/report.xml

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000449_10/reports/complex_pose_2/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1hny/PE000449_10/re

...

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000843_1/reports/complex_pose_6/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000843_1/reports/complex_pose_7/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000843_1/reports/complex_pose_8/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000843_1/reports/complex_pose_9/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000843_2/reports/complex_pose_1/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000843_2/reports/complex_pose_2/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000843_2/reports/complex_pose_3/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000843_2/reports/complex_pose_4/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000843_2/reports/complex_pose_5/report.xml

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000843_2/repo

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_108/reports/complex_pose_5/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_108/reports/complex_pose_6/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_108/reports/complex_pose_7/report.xml

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_108/reports/complex_pose_8/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_108/reports/complex_pose_9/report.xml

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_109/reports/complex_pose_1/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_109/reports/complex_pose_2/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_109/reports/complex_pose_3/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_109/reports/complex_pose_4/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1o

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_255/reports/complex_pose_4/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_255/reports/complex_pose_5/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_255/reports/complex_pose_6/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_255/reports/complex_pose_7/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_255/reports/complex_pose_8/report.xml

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_255/reports/complex_pose_9/report.xml

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_256/reports/complex_pose_1/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_256/reports/complex_pose_2/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_256/reports/complex_pose_3/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1os

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_400/reports/complex_pose_6/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_400/reports/complex_pose_7/report.xml

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_400/reports/complex_pose_8/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_400/reports/complex_pose_9/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_401/reports/complex_pose_1/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_401/reports/complex_pose_2/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_401/reports/complex_pose_3/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_401/reports/complex_pose_4/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE000925_401/reports/complex_pose_5/report.xml


/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1o

/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001010_4/reports/complex_pose_5/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001010_4/reports/complex_pose_6/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001010_4/reports/complex_pose_7/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001010_4/reports/complex_pose_8/report.xml
/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001010_4/reports/complex_pose_9/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001011_1/reports/complex_pose_1/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001011_1/reports/complex_pose_2/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001011_1/reports/complex_pose_3/report.xml



/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001011_1/reports/complex_pose_4/report.xml/mnt/e/works/polyphenol_vscreening/docking_runs_vina/1ose/PE001011_1/repor

In [ ]:
collection = db['interaction_reports']
for receptordir in receptor_dirs:
    with open(f"../docking_runs_vina/{receptordir}/{LIGAND_DIR_LIST_FILENAME}") as listfile:
        for line in listfile:
            line = line.rstrip("\n")
            reports_dir_path = f"../docking_runs_vina/{receptordir}/{line}/reports"
            if os.path.exists(reports_dir_path):
                report_dirs = [name for name in os.listdir(reports_dir_path) if os.path.isdir(os.path.join(reports_dir_path, name))]
                for report in report_dirs:
                    add_report(receptordir, line, report)

# Insert docking scores

In [ ]:
# collect_result_from_vina_log("1ose", "PE000008_1")

In [27]:
pose_col = db['docking_scores']
for receptordir in receptor_dirs:
    with open(f"../docking_runs_vina/{receptordir}/{LIGAND_DIR_LIST_FILENAME}") as listfile:
        for line in listfile:
            line = line.rstrip("\n")
            poses = collect_result_from_vina_log(receptordir, line)
            if poses is not None:
                pose_col.insert_many(poses)

Docking Result Table not found for 1hny > PE000928_1
Docking Result Table not found for 1lpb > PE000928_1
Docking Result Table not found for 1ose > PE000928_1


In [33]:
len(bs[0]['interactions']['hydrophobic_interactions'])

6